In [1]:
# import Libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

import warnings
warnings.simplefilter('ignore')


from scipy.special import boxcox1p
from scipy import stats

In [2]:
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import learning_curve,cross_val_score,validation_curve,train_test_split
from sklearn.tree import DecisionTreeRegressor
from sklearn.linear_model import LogisticRegression
from sklearn.linear_model import SGDClassifier
from sklearn.svm import LinearSVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import precision_recall_curve
from sklearn.metrics import roc_auc_score
from sklearn import linear_model

In [3]:
# Load Data
data = pd.read_excel('WA_Fn-UseC_-Telco-Customer-Churn.xlsx', index_col = 0)
data.head()

gender  SeniorCitizen Partner Dependents  tenure PhoneService  \
customerID                                                                  
7590-VHVEG  Female              0     Yes         No       1           No   
5575-GNVDE    Male              0      No         No      34          Yes   
3668-QPYBK    Male              0      No         No       2          Yes   
7795-CFOCW    Male              0      No         No      45           No   
9237-HQITU  Female              0      No         No       2          Yes   

               MultipleLines InternetService OnlineSecurity OnlineBackup  \
customerID                                                                 
7590-VHVEG  No phone service             DSL             No          Yes   
5575-GNVDE                No             DSL            Yes           No   
3668-QPYBK                No             DSL            Yes          Yes   
7795-CFOCW  No phone service             DSL            Yes           No   
9237-HQITU                No     Fiber optic             No           No   

           DeviceProtection TechSupport StreamingTV StreamingMovies  \
customerID                                                            
7590-VHVEG               No          No          No              No   
5575-GNVDE              Yes          No          No              No   
3668-QPYBK               No          No          No              No   
7795-CFOCW              Yes         Yes          No              No   
9237-HQITU               No          No          No              No   

                  Contract PaperlessBilling              PaymentMethod  \
customerID                                                               
7590-VHVEG  Month-to-month              Yes           Electronic check   
5575-GNVDE        One year               No               Mailed check   
3668-QPYBK  Month-to-month              Yes               Mailed check   
7795-CFOCW        One year               No  Bank transfer (automatic)   
9237-HQITU  Month-to-month              Yes           Electronic check   

            MonthlyCharges TotalCharges Churn  
customerID                                     
7590-VHVEG           29.85        29.85    No  
5575-GNVDE           56.95       1889.5    No  
3668-QPYBK           53.85       108.15   Yes  
7795-CFOCW           42.30      1840.75    No  
9237-HQITU           70.70       151.65   Yes

In [4]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 7043 entries, 7590-VHVEG to 3186-AJIEK
Data columns (total 20 columns):
gender              7043 non-null object
SeniorCitizen       7043 non-null int64
Partner             7043 non-null object
Dependents          7043 non-null object
tenure              7043 non-null int64
PhoneService        7043 non-null object
MultipleLines       7043 non-null object
InternetService     7043 non-null object
OnlineSecurity      7043 non-null object
OnlineBackup        7043 non-null object
DeviceProtection    7043 non-null object
TechSupport         7043 non-null object
StreamingTV         7043 non-null object
StreamingMovies     7043 non-null object
Contract            7043 non-null object
PaperlessBilling    7043 non-null object
PaymentMethod       7043 non-null object
MonthlyCharges      7043 non-null float64
TotalCharges        7043 non-null object
Churn               7043 non-null object
dtypes: float64(1), int64(2), object(17)
memory usage: 1.1+ MB


In [18]:
# rename columns which have inconsistency
data.rename(columns = {'tenure': 'Tenure', 'gender':'Gender'}, inplace = True)

#### Removing Mismatch values

In [5]:
col = ['MultipleLines','OnlineSecurity','OnlineBackup','DeviceProtection','TechSupport','StreamingTV']
for col in col:
    data.replace(to_replace = {'No phone service':'No', 'No internet service':'No'}, inplace = True)

In [6]:
# separate numerical and categorical features
num = ['Tenure','MonthlyCharges', 'TotalCharges']
categorical = [c for c in data.columns if c not in num]

In [8]:
# function to convert categorical features into dummy variables
def getdummies(col, df):
    for col in col:
        df[col] = pd.get_dummies(df[col], drop_first = True, dtype = 'int')
    return df

data = getdummies(categorical, data)

In [9]:
# checking the conversion of data types
data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 7043 entries, 7590-VHVEG to 3186-AJIEK
Data columns (total 20 columns):
gender              7043 non-null int32
SeniorCitizen       7043 non-null int32
Partner             7043 non-null int32
Dependents          7043 non-null int32
tenure              7043 non-null int32
PhoneService        7043 non-null int32
MultipleLines       7043 non-null int32
InternetService     7043 non-null int32
OnlineSecurity      7043 non-null int32
OnlineBackup        7043 non-null int32
DeviceProtection    7043 non-null int32
TechSupport         7043 non-null int32
StreamingTV         7043 non-null int32
StreamingMovies     7043 non-null int32
Contract            7043 non-null int32
PaperlessBilling    7043 non-null int32
PaymentMethod       7043 non-null int32
MonthlyCharges      7043 non-null float64
TotalCharges        7043 non-null object
Churn               7043 non-null int32
dtypes: float64(1), int32(18), object(1)
memory usage: 660.3+ KB


On close inspection of TotalCharges columns, I found that some entries are missing and only space is available, so dtype of Totalcharges is object. Lets check the index of faulty entries.

##### Faulty entries removal

In [10]:
index = data[data['TotalCharges'].isin([' '])]
index[['PhoneService', 'MonthlyCharges', 'TotalCharges']]

PhoneService  MonthlyCharges TotalCharges
customerID                                           
4472-LVYGI             0           52.55             
3115-CZMZD             1           20.25             
5709-LVOEQ             1           80.85             
4367-NUYAO             1           25.75             
1371-DWPAZ             0           56.05             
7644-OMVMY             1           19.85             
3213-VVOLG             1           25.35             
2520-SGTTA             1           20.00             
2923-ARZLG             1           19.70             
4075-WKNIU             1           73.35             
2775-SEFEE             1           61.90

In [11]:
data.drop(data[data.TotalCharges == ' '].index, inplace = True)

data['TotalCharges'] = data['TotalCharges'].astype('float64')

data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 7032 entries, 7590-VHVEG to 3186-AJIEK
Data columns (total 20 columns):
gender              7032 non-null int32
SeniorCitizen       7032 non-null int32
Partner             7032 non-null int32
Dependents          7032 non-null int32
tenure              7032 non-null int32
PhoneService        7032 non-null int32
MultipleLines       7032 non-null int32
InternetService     7032 non-null int32
OnlineSecurity      7032 non-null int32
OnlineBackup        7032 non-null int32
DeviceProtection    7032 non-null int32
TechSupport         7032 non-null int32
StreamingTV         7032 non-null int32
StreamingMovies     7032 non-null int32
Contract            7032 non-null int32
PaperlessBilling    7032 non-null int32
PaymentMethod       7032 non-null int32
MonthlyCharges      7032 non-null float64
TotalCharges        7032 non-null float64
Churn               7032 non-null int32
dtypes: float64(2), int32(18)
memory usage: 659.2+ KB


In [ ]:
data.head()

#### Summary Statistics

In [ ]:
data.describe()

In [12]:
corr_matrix = data.corr()
corr_matrix['Churn'].sort_values(ascending = False)

Churn               1.000000
InternetService     0.307463
tenure              0.247723
MonthlyCharges      0.192858
PaperlessBilling    0.191454
SeniorCitizen       0.150541
StreamingTV         0.063254
StreamingMovies     0.060860
MultipleLines       0.040033
PhoneService        0.011691
gender             -0.008545
DeviceProtection   -0.066193
OnlineBackup       -0.082307
PaymentMethod      -0.134687
Partner            -0.149982
Dependents         -0.163128
TechSupport        -0.164716
OnlineSecurity     -0.171270
Contract           -0.178225
TotalCharges       -0.199484
Name: Churn, dtype: float64

corr_matrix shows InternetService, Monthly charges, PaperlessBilling, SeniorCitizen have positive correlation with label and Tenure and many other columns have strong negative correlation with label.

I have analysed categorical variables in Tableau and observed StreamingTv and SteamingMovies columns are identical and corr_matrix shows same correlation. Lets verify it with assert statement.

#### Removing Duplicate Columns

In [13]:
assert data.StreamingTV.all() == data.StreamingMovies.all()

As each data value is same in both columns, its better to remove one column.

In [14]:
data.drop(['StreamingMovies'], axis = 1, inplace = True )

#### Plot frequency counts of categorical variables

In [ ]:
data['SeniorCitizen'].value_counts().plot.bar(title = 'Freq. Distribution of SeniorCitizen')

In [ ]:
data['PhoneService'].value_counts().plot.bar(title = 'Freq. Distribution of PhoneService')

In [ ]:
data['TechSupport'].value_counts().plot.bar(title = 'Freq. Distribution of TechSupport')

SeniorCitizen variable, online backup, online security are imbalanced variables.

** Findings from Tableau **
* Gender has insignificant impact on label as female and male churn is almost equal.
* Those who have No internet service are likely to stay.
* TechSupport is also Imbalanced and Those who take Techsupport are likely to stay.
* StreamingTv is almost balanced and Those who take this facility are likely to stay.
* SeniorCitizen variable is highly imbalanced and those who are SeniorCitizen are likely to leave.
* PhoneService does not have much impact on churn.
* PaymentMethod is balanced and those with Electronic check method and mailed check likely to leave in the same order.
* Partner is balanced and One with who have partner is likely to stay.
* Paperless billing is slightly imbalanced(~1000) and those who have paperless billing are likely to leave.
* Those who have online Security are likely to stay.
* Those who have Fibre Optics are likely to leave.
* DeviceProtection has slight impact with those who have are likely to stay.
* Those who are dependents are likely to stay.
* Those who have month_to_month contract are more likely to leave > one year> 2 year.

#### Check Distribution of Numerical Columns

In [ ]:
col_name = ['Tenure', 'TotalCharges', 'MonthlyCharges']
fig, ax = plt.subplots(len(col_name), figsize = (12,8))
for i, col in enumerate(col_name):
    sns.distplot(data[col], hist  = True, kde = True, ax = ax[i])
    ax[i].set_title('Freq dist '+col, fontsize=10)
    ax[i].set_xlabel(col, fontsize=8)
    ax[i].set_ylabel('Count', fontsize=8)
    
plt.tight_layout()    
plt.show()

TotalCharges are highly right skewed and it also have some outliers. Lets verify the presence of outlier using IQR method.

#### Outlier Detection

In [ ]:
def detect_outlier(df_in, col_name):
    q1 = df_in[col_name].quantile(0.25)
    q3 = df_in[col_name].quantile(0.75)
    iqr = q3-q1 #Interquartile range
    fence_low  = q1-1.5*iqr
    fence_high = q3+1.5*iqr
    lower_outer_fence = q1 - 3*iqr
    upper_outer_fence = q3 + 3*iqr
    mild_outlier = df_in.loc[(df_in[col_name] < fence_low) & (df_in[col_name] > fence_high)]
    extreme_outlier = df_in.loc[(df_in[col_name] < lower_outer_fence) & (df_in[col_name] > upper_outer_fence)]
    return (mild_outlier, extreme_outlier)
mild_outlier, extreme_outlier = detect_outlier(data, 'TotalCharges')

In [ ]:
scatter_col = ['MonthlyCharges', 'TotalCharges']
sns.pairplot(data[scatter_col])
plt.show()

As MonthlyCharges and TotalCharges are strongly correlated, its better to remove one column. I will remove after checking p value with gretl. Gretl shows p value is lower for TotalCharges, so I will drop monthly charges column.

In [15]:
data.drop('MonthlyCharges', axis = 'columns', inplace = True)

In [ ]:
# bins = [0,6,12,18,24,30,36,42,48,54,60,66,72]
# print(bins)
# Tenure_bin = pd.cut(data.Tenure,bins)
# Tenure_bin = Tenure_bin.to_frame()
# Tenure_bin.columns = ['Tenure_bin']
# #concatenate data and Tenure bin
# pd.concat([data, Tenure_bin], axis = 1)
# print(Tenure_bin.dtype)

In [ ]:
# fig, ax = plt.subplots(len(data.columns), figsize=(8,40))

# for i, col_val in enumerate(data.columns):

#     sns.boxplot(y=data[col_val], ax=ax[i])
#     ax[i].set_title('Box plot - {}'.format(col_val), fontsize=10)
#     ax[i].set_xlabel(col_val, fontsize=8)

# plt.tight_layout()
# plt.show()

Get **skewness** of features

In [19]:
num = ['TotalCharges', 'Tenure']
skewness = []
for i in num:
    skewness.append(data[i].skew())
pd.DataFrame(data = skewness, index = num, columns = ['skewness']).sort_values(by = 'skewness',ascending = False)

skewness
Tenure        2.927560
TotalCharges  0.961642

As TotalCharges have high skew, its important to transform it. I am trying two methods, boxcox transformation and binning. I am using Tableau for Binning visuallization.

#### Boxcox Transformation

In [20]:
xt, maxlog, interval = stats.boxcox(data['TotalCharges'], alpha=0.05)
print("lambda = {:g}".format(maxlog))

from astropy.table import Table


def normtesttab(x):
    nm_value, nm_p = stats.normaltest(x)
    jb_value, jb_p = stats.jarque_bera(x)
    data_rows = [('D’Agostino-Pearson', nm_value, nm_p),
                 ('Jarque-Bera', jb_value, jb_p)]
    t = Table(rows=data_rows, names=('Test name', 'Statistic', 'p-value'), 
              meta={'name': 'normal test table'},
          dtype=('S25', 'f8', 'f8'))
    print(t)
    
normtesttab(xt)

lambda = 0.254765
    Test name          Statistic      p-value
------------------ ------------------ -------
D’Agostino-Pearson 2035.5642962844804     0.0
       Jarque-Bera 342.66936486137655     0.0


In [21]:
data['TotalCharges'] = data['TotalCharges'].apply(lambda x: boxcox1p(x,0.25))

data['TotalCharges'].skew()

-0.15188360617572969

#### Split Data

In [22]:
X = data.drop('Churn', axis = 1)
y = data['Churn']
X_train, X_test, y_train, y_test = train_test_split(X, y ,random_state = 42, test_size = 0.3, stratify = y)
X_train.shape, X_test.shape, y_train.shape, y_test.shape

((4922, 17), (2110, 17), (4922,), (2110,))

#### Scaling

In [24]:
scaler = StandardScaler()
scaler.fit_transform(X_train)
scaler.fit_transform(X_test)

array([[ 0.97657755, -0.43981691, -0.95277267, ..., -1.19385399,
         1.92336472, -1.94089345],
       [-1.02398422, -0.43981691,  1.0495683 , ..., -1.19385399,
        -0.51992219, -0.89616154],
       [-1.02398422,  2.27367338,  1.0495683 , ...,  0.83762337,
        -0.51992219,  1.6572947 ],
       ...,
       [ 0.97657755, -0.43981691, -0.95277267, ..., -1.19385399,
        -0.51992219,  0.61901661],
       [-1.02398422, -0.43981691,  1.0495683 , ..., -1.19385399,
        -0.51992219, -0.71359771],
       [ 0.97657755,  2.27367338, -0.95277267, ...,  0.83762337,
        -0.51992219,  0.97850486]])

#### Evaluate score of some selected classifiers

In [ ]:
def get_score(model, X_train, y_train):
    model.fit(X_train,y_train)
    return model.score(X_train, y_train)

print('Logistic Regression: ',get_score(LogisticRegression(), X_train, y_train))
print('SGD: ', get_score(SGDClassifier(), X_train, y_train))
print('LinearSVC: ', get_score(LinearSVC(), X_train, y_train))
print('RandomForest: ',get_score(RandomForestClassifier(), X_train, y_train))
print('DecisionTree: ', get_score(DecisionTreeClassifier(), X_train, y_train))
print('Naive Bayes: ', get_score(GaussianNB(), X_train, y_train))

In [ ]:
clf = LogisticRegression()
logistic_score = cross_val_score(clf, X_train, y_train, cv = 3)
print('l_mean: ',logistic_score.mean())
print('L_std: ',logistic_score.std())

clf = SGDClassifier()
SGDC_score = cross_val_score(clf, X_train, y_train, cv = 3)
print('SGDC mean: ',SGDC_score.mean())
print('SGDC_std: ',SGDC_score.std())

clf = LinearSVC()
SVC = cross_val_score(clf, X_train, y_train, cv = 3)
print('SVC_mean:', SVC.mean())
print('SVC_std:', SVC.std())

clf = RandomForestClassifier()
Random_score = cross_val_score(clf, X_train, y_train, cv = 3)
print('Random_mean:', Random_score.mean())
print('Random_std:', Random_score.std())

clf = DecisionTreeClassifier()
tree_score = cross_val_score(clf, X_train, y_train, cv = 3)
print('tree_mean: ', tree_score.mean())
print('tree_std: ', tree_score.std())

clf = GaussianNB()
naive_score = cross_val_score(clf, X_train, y_train, cv = 3)
print('naive_mean: ' ,naive_score.mean())
print('naive_std: ', naive_score.std())

clf = KNeighborsClassifier()
KNN_score = cross_val_score(clf, X_train, y_train, cv = 3)
print('Knn_mean: ',KNN_score.mean())
print('Knn_std: ', KNN_score.std())


So, It seems like LogisticRegression and RandomForest works best on this dataset but variance is very low in both these classifiers which is a very good thing.

In [ ]:
clf = RandomForestClassifier()
grid_param = {  
    'n_estimators': [100, 300, 500, 800, 1000],
    'criterion': ['gini', 'entropy'],
    'bootstrap': [True, False],
}

gd_sr = GridSearchCV(estimator=clf,  
                     param_grid=grid_param,
                     scoring='accuracy',
                     cv=5,
                     n_jobs=-1)

gd_sr.fit(X_train, y_train)  

In [ ]:
best_parameters = gd_sr.best_params_  
print(best_parameters)  

In [ ]:
best_result = gd_sr.best_score_  
print(best_result)  

In [ ]:
clf = LogisticRegression()
grid_param = {
            'penalty': ['l1', 'l2'],
            'C': [1,3,10,50,100,1000],
            }
gd_sr = GridSearchCV(estimator=clf,  
                     param_grid=grid_param,
                     scoring='roc_auc',
                     cv=5,
                     n_jobs=-1)

gd_sr.fit(X_train, y_train) 

best_parameters = gd_sr.best_params_  
print(best_parameters)  

In [ ]:
best_result = gd_sr.best_score_  
print(best_result)  

In [ ]:
clf = LogisticRegression()
from sklearn.model_selection import cross_val_predict
y_pred = cross_val_predict(clf, X_train, y_train, cv = 3)

In [ ]:
from sklearn.metrics import confusion_matrix
confusion_matrix(y_train, y_pred)

In [ ]:
from sklearn.metrics import precision_score, recall_score
from sklearn.metrics import f1_score
print(precision_score(y_train, y_pred))
print(recall_score(y_train, y_pred))
print(f1_score(y_train, y_pred))

In [ ]:
from sklearn.metrics import precision_recall_curve
precisions, recalls, thresholds = precision_recall_curve(y_train, y_pred)

def plot_precision_recall_vs_threshold(precisions, recalls, thresholds):
    plt.plot(thresholds, precisions[:-1], "b--", label="Precision")
    plt.plot(thresholds, recalls[:-1], "g-", label="Recall")
    plt.xlabel("Threshold")
    plt.legend(loc="upper left")
    plt.ylim([0, 1])
plot_precision_recall_vs_threshold(precisions, recalls, thresholds)
plt.show()

In [ ]:
from sklearn.metrics import roc_curve
fpr, tpr, thresholds = roc_curve(y_train, y_pred)

def plot_roc_curve(fpr, tpr, label=None):
    plt.plot(fpr, tpr, linewidth=2, label=label)
    plt.plot([0, 1], [0, 1], 'k--')
    plt.axis([0, 1, 0, 1])
    plt.xlabel('False Positive Rate')
    plt.ylabel('True Positive Rate')
plot_roc_curve(fpr, tpr)
plt.show()

#### Artificial Neural Network

In [25]:
import keras
from keras.layers import Dense
from keras.models import Sequential
from keras.wrappers.scikit_learn import KerasClassifier
from keras.layers import Dropout
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import cross_val_score

In [38]:
def ann_architecture(optimizer, unit):
    clf = Sequential()
    clf.add(Dense(units = unit, input_dim = 17, activation = 'relu', kernel_initializer = 'uniform'))
    clf.add(Dropout(p = 0.1))
    clf.add(Dense(units = 1, activation = 'sigmoid', kernel_initializer = 'uniform'))
    clf.compile(optimizer = optimizer, loss = 'binary_crossentropy', metrics = ['accuracy'])
    return clf

In [39]:
classifier = KerasClassifier(build_fn= ann_architecture)
parameters = {'batch_size': [10, 25, 32],
             'epochs': [100, 500],
             'optimizer':['adam','rmsprop'],
              'unit': [9, 12, 15],
}
grid = GridSearchCV(estimator= classifier, param_grid= parameters, scoring= 'accuracy', cv = 10)
grid = grid.fit(X_train, y_train)
best_parameters = grid.best_params_
best_accuracy = grid.best_score_

Epoch 1/100
4429/4429 [==============================] - 1s 262us/step - loss: 0.5508 - acc: 0.7385
Epoch 2/100
4429/4429 [==============================] - 1s 132us/step - loss: 0.4814 - acc: 0.7758
Epoch 3/100
4429/4429 [==============================] - 1s 133us/step - loss: 0.4486 - acc: 0.7961
Epoch 4/100
4429/4429 [==============================] - 1s 129us/step - loss: 0.4402 - acc: 0.7972
Epoch 5/100
4429/4429 [==============================] - 1s 134us/step - loss: 0.4389 - acc: 0.8006
Epoch 6/100
4429/4429 [==============================] - 1s 131us/step - loss: 0.4360 - acc: 0.8029
Epoch 7/100
4429/4429 [==============================] - 1s 133us/step - loss: 0.4308 - acc: 0.8097
Epoch 8/100
4429/4429 [==============================] - 1s 132us/step - loss: 0.4324 - acc: 0.8015
Epoch 9/100
4429/4429 [==============================] - 1s 133us/step - loss: 0.4315 - acc: 0.8020
Epoch 10/100
4429/4429 [==============================] - 1s 138us/step - loss: 0.4329 - acc: 0.8009

4429/4429 [==============================] - 1s 130us/step - loss: 0.4180 - acc: 0.8072
Epoch 82/100
4429/4429 [==============================] - 1s 130us/step - loss: 0.4205 - acc: 0.8108
Epoch 83/100
4429/4429 [==============================] - 1s 125us/step - loss: 0.4199 - acc: 0.8112
Epoch 84/100
4429/4429 [==============================] - 1s 131us/step - loss: 0.4204 - acc: 0.8083
Epoch 85/100
4429/4429 [==============================] - 1s 130us/step - loss: 0.4217 - acc: 0.8103
Epoch 86/100
4429/4429 [==============================] - 1s 128us/step - loss: 0.4202 - acc: 0.8110
Epoch 87/100
4429/4429 [==============================] - 1s 125us/step - loss: 0.4213 - acc: 0.8061
Epoch 88/100
4429/4429 [==============================] - 1s 128us/step - loss: 0.4199 - acc: 0.8101
Epoch 89/100
4429/4429 [==============================] - 1s 160us/step - loss: 0.4254 - acc: 0.8049
Epoch 90/100
4429/4429 [==============================] - 1s 125us/step - loss: 0.4182 - acc: 0.8151
Epo

4429/4429 [==============================] - 1s 139us/step - loss: 0.4378 - acc: 0.8020
Epoch 62/100
4429/4429 [==============================] - 1s 125us/step - loss: 0.4383 - acc: 0.8002
Epoch 63/100
4429/4429 [==============================] - 1s 131us/step - loss: 0.4374 - acc: 0.8002
Epoch 64/100
4429/4429 [==============================] - 1s 126us/step - loss: 0.4394 - acc: 0.8015
Epoch 65/100
4429/4429 [==============================] - 1s 132us/step - loss: 0.4351 - acc: 0.8070
Epoch 66/100
4429/4429 [==============================] - 1s 125us/step - loss: 0.4371 - acc: 0.8054
Epoch 67/100
4429/4429 [==============================] - 1s 134us/step - loss: 0.4357 - acc: 0.8022
Epoch 68/100
4429/4429 [==============================] - 1s 130us/step - loss: 0.4366 - acc: 0.8011
Epoch 69/100
4429/4429 [==============================] - 1s 136us/step - loss: 0.4324 - acc: 0.8027
Epoch 70/100
4429/4429 [==============================] - 1s 130us/step - loss: 0.4335 - acc: 0.8036
Epo

4430/4430 [==============================] - 1s 140us/step - loss: 0.4339 - acc: 0.8045
Epoch 43/100
4430/4430 [==============================] - 1s 138us/step - loss: 0.4318 - acc: 0.8068
Epoch 44/100
4430/4430 [==============================] - 1s 139us/step - loss: 0.4306 - acc: 0.8050
Epoch 45/100
4430/4430 [==============================] - 1s 139us/step - loss: 0.4324 - acc: 0.8045
Epoch 46/100
4430/4430 [==============================] - 1s 127us/step - loss: 0.4326 - acc: 0.8072
Epoch 47/100
4430/4430 [==============================] - 1s 126us/step - loss: 0.4320 - acc: 0.8052
Epoch 48/100
4430/4430 [==============================] - 1s 145us/step - loss: 0.4262 - acc: 0.8059 0s - loss: 0.4212 - acc: 0
Epoch 49/100
4430/4430 [==============================] - 1s 145us/step - loss: 0.4356 - acc: 0.8029
Epoch 50/100
4430/4430 [==============================] - 1s 138us/step - loss: 0.4335 - acc: 0.8041
Epoch 51/100
4430/4430 [==============================] - 1s 138us/step - los

4430/4430 [==============================] - 1s 125us/step - loss: 0.4454 - acc: 0.7975
Epoch 23/100
4430/4430 [==============================] - 1s 123us/step - loss: 0.4444 - acc: 0.8000
Epoch 24/100
4430/4430 [==============================] - 1s 128us/step - loss: 0.4419 - acc: 0.7975
Epoch 25/100
4430/4430 [==============================] - 1s 124us/step - loss: 0.4445 - acc: 0.8011
Epoch 26/100
4430/4430 [==============================] - 1s 126us/step - loss: 0.4444 - acc: 0.7986
Epoch 27/100
4430/4430 [==============================] - 1s 125us/step - loss: 0.4447 - acc: 0.8023
Epoch 28/100
4430/4430 [==============================] - 1s 123us/step - loss: 0.4428 - acc: 0.8007
Epoch 29/100
4430/4430 [==============================] - 1s 124us/step - loss: 0.4423 - acc: 0.8009
Epoch 30/100
4430/4430 [==============================] - 1s 124us/step - loss: 0.4404 - acc: 0.8009
Epoch 31/100
4430/4430 [==============================] - 1s 127us/step - loss: 0.4452 - acc: 0.7977
Epo

...

4430/4430 [==============================] - 1s 135us/step - loss: 0.4357 - acc: 0.8072
Epoch 64/100
4430/4430 [==============================] - 1s 133us/step - loss: 0.4335 - acc: 0.8086
Epoch 65/100
4430/4430 [==============================] - 1s 133us/step - loss: 0.4367 - acc: 0.8081
Epoch 66/100
4430/4430 [==============================] - 1s 134us/step - loss: 0.4338 - acc: 0.8095
Epoch 67/100
4430/4430 [==============================] - 1s 130us/step - loss: 0.4377 - acc: 0.8023
Epoch 68/100
4430/4430 [==============================] - 1s 128us/step - loss: 0.4362 - acc: 0.8074
Epoch 69/100
4430/4430 [==============================] - 1s 133us/step - loss: 0.4367 - acc: 0.8074
Epoch 70/100
4430/4430 [==============================] - 1s 131us/step - loss: 0.4389 - acc: 0.8034
Epoch 71/100
4430/4430 [==============================] - 1s 132us/step - loss: 0.4382 - acc: 0.8081
Epoch 72/100
4430/4430 [==============================] - 1s 132us/step - loss: 0.4371 - acc: 0.8063
Epo

4430/4430 [==============================] - 1s 129us/step - loss: 0.4345 - acc: 0.8065
Epoch 45/100
4430/4430 [==============================] - 1s 128us/step - loss: 0.4330 - acc: 0.8050
Epoch 46/100
4430/4430 [==============================] - 1s 130us/step - loss: 0.4346 - acc: 0.8054
Epoch 47/100
4430/4430 [==============================] - 1s 129us/step - loss: 0.4354 - acc: 0.8036
Epoch 48/100
4430/4430 [==============================] - 1s 131us/step - loss: 0.4367 - acc: 0.8059
Epoch 49/100
4430/4430 [==============================] - 1s 128us/step - loss: 0.4351 - acc: 0.8068
Epoch 50/100
4430/4430 [==============================] - 1s 127us/step - loss: 0.4350 - acc: 0.8023
Epoch 51/100
4430/4430 [==============================] - 1s 126us/step - loss: 0.4343 - acc: 0.8056
Epoch 52/100
4430/4430 [==============================] - 1s 129us/step - loss: 0.4307 - acc: 0.8063
Epoch 53/100
4430/4430 [==============================] - 1s 129us/step - loss: 0.4325 - acc: 0.8063
Epo

4430/4430 [==============================] - 1s 132us/step - loss: 0.4337 - acc: 0.8050
Epoch 26/100
4430/4430 [==============================] - 1s 128us/step - loss: 0.4340 - acc: 0.8065
Epoch 27/100
4430/4430 [==============================] - 1s 130us/step - loss: 0.4360 - acc: 0.8086
Epoch 28/100
4430/4430 [==============================] - 1s 134us/step - loss: 0.4335 - acc: 0.8077
Epoch 29/100
4430/4430 [==============================] - 1s 130us/step - loss: 0.4360 - acc: 0.8068
Epoch 30/100
4430/4430 [==============================] - 1s 128us/step - loss: 0.4357 - acc: 0.8065
Epoch 31/100
4430/4430 [==============================] - 1s 131us/step - loss: 0.4343 - acc: 0.8027
Epoch 32/100
4430/4430 [==============================] - 1s 129us/step - loss: 0.4353 - acc: 0.8054
Epoch 33/100
4430/4430 [==============================] - 1s 127us/step - loss: 0.4320 - acc: 0.8084
Epoch 34/100
4430/4430 [==============================] - 1s 131us/step - loss: 0.4329 - acc: 0.8054
Epo

4430/4430 [==============================] - 1s 131us/step - loss: 0.4656 - acc: 0.7930
Epoch 7/100
4430/4430 [==============================] - 1s 131us/step - loss: 0.4564 - acc: 0.8029
Epoch 8/100
4430/4430 [==============================] - 1s 130us/step - loss: 0.4499 - acc: 0.8045
Epoch 9/100
4430/4430 [==============================] - 1s 128us/step - loss: 0.4468 - acc: 0.8029
Epoch 10/100
4430/4430 [==============================] - 1s 132us/step - loss: 0.4449 - acc: 0.8016
Epoch 11/100
4430/4430 [==============================] - 1s 129us/step - loss: 0.4473 - acc: 0.8016
Epoch 12/100
4430/4430 [==============================] - 1s 132us/step - loss: 0.4421 - acc: 0.8029
Epoch 13/100
4430/4430 [==============================] - 1s 130us/step - loss: 0.4423 - acc: 0.8036
Epoch 14/100
4430/4430 [==============================] - 1s 131us/step - loss: 0.4431 - acc: 0.8018
Epoch 15/100
4430/4430 [==============================] - 1s 132us/step - loss: 0.4410 - acc: 0.8018
Epoch 

KeyboardInterrupt: 